# Importing & Loading Dependencies

In [1]:
!pip install monai
# !pip install 'monai[nibabel]'

import nibabel as nib
from monai.transforms import LoadImage, Compose, NormalizeIntensityd, RandFlipd, RandAdjustContrastd, Resized,  CropForegroundd, SpatialPadd
import matplotlib.pyplot as plt
from torch.utils.data import DataLoader, Dataset
import torch
import torch.nn as nn
import torch.nn.functional as F
import numpy as np
from typing import Optional, Sequence, Tuple, Union
from torch.nn.functional import interpolate

from monai.networks.blocks.convolutions import Convolution
from monai.networks.layers.factories import Act, Norm
from monai.networks.layers.utils import get_act_layer, get_norm_layer
from monai.metrics import DiceMetric, HausdorffDistanceMetric

from torch import nn, optim, amp
from itertools import chain
from monai.losses import DiceLoss

from tqdm import tqdm
from pathlib import Path
import math
import os
import random

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 18.9 MB/s eta 0:00:00


# Creating Dataset with Preprocessing

In [2]:
class CustomDataset3D(Dataset):
    def __init__(self, data_dirs, patient_lists, mode):
        self.data_dirs = data_dirs
        self.patient_lists = patient_lists
        self.mode = mode

    @staticmethod
    def resize_with_aspect_ratio(keys, target_size):
        def transform(data):
            for key in keys:
                volume = data[key]
                original_shape = volume.shape[-3:]
    
                scaling_factor = min(
                    target_size[0] / original_shape[0],
                    target_size[1] / original_shape[1],
                    target_size[2] / original_shape[2]
                )
    
                # Computing the intermediate size while preserving aspect ratio
                new_shape = [
                    int(dim * scaling_factor) for dim in original_shape
                ]
    
                # Resizing to the intermediate shape
                resize_transform = Resized(keys=[key], spatial_size=new_shape, mode="trilinear" if key == "imgs" else "nearest-exact")
                data = resize_transform(data)
    
                # Padding to the final target size
                pad_transform = SpatialPadd(keys=[key], spatial_size=target_size, mode="constant")
                data = pad_transform(data)
            return data

        return transform

    def preprocess(cls, data, mode):
        if mode == 'training':
          transform = Compose([
            CropForegroundd(keys=["imgs", "masks"], source_key="imgs"),
            cls.resize_with_aspect_ratio(keys=["imgs", "masks"], target_size=[128, 128, 128]),
            NormalizeIntensityd( keys=['imgs'], nonzero=False, channel_wise=True),
              
            RandFlipd(keys=["imgs", "masks"],   
                    prob=0.5,                 
                    spatial_axis=2,  
            ),

            RandAdjustContrastd(
                keys=["imgs"],          
                prob=0.15,             
                gamma=(0.65, 1.5),   
            ),
            
        ])

        elif mode == 'validation':
          transform = Compose([
            CropForegroundd(keys=["imgs", "masks"], source_key="imgs"),
            cls.resize_with_aspect_ratio(keys=["imgs", "masks"], target_size=[128, 128, 128]),
            NormalizeIntensityd( keys=['imgs'], nonzero=False, channel_wise=True)

        ])

        else: # 'testing'
          transform = Compose([
            CropForegroundd(keys=["imgs", "masks"], source_key="imgs"),
            cls.resize_with_aspect_ratio(keys=["imgs", "masks"], target_size=[128, 128, 128]),
            NormalizeIntensityd( keys=['imgs'], nonzero=False, channel_wise=True)

        ])

        augmented_data = transform(data)
        return augmented_data
        
    def __len__(self):
        return len(self.patient_lists)

    def __getitem__(self, idx):
        patient_id = self.patient_lists[idx]
        loadimage = LoadImage(reader='NibabelReader', image_only=True)

        data_type=patient_id.split('-')[1]
        if data_type == 'GLI':
            patient_folder_path = os.path.join('/kaggle/input/bratsglioma/Training', patient_id)
        elif data_type == 'SSA':
            patient_folder_path = os.path.join('/kaggle/input/bratsafrica24', patient_id)
        elif data_type == 'PED':
            patient_folder_path = os.path.join('/kaggle/input/bratsped/Training', patient_id)
        elif data_type == 'MEN':
            patient_folder_path = os.path.join('/kaggle/input/bratsmen', patient_id)
        else:
            patient_folder_path = os.path.join('/kaggle/input/bratsmet24', patient_id)

        def resolve_file_path(folder, name):
            file_path = os.path.join(folder, name)
            # Check if the given path is a directory (case with 4 subdirs)
            if os.path.isdir(file_path):
                # Find the first file inside the directory that ends with .nii
                for root, _, files in os.walk(file_path):
                    for file in files:
                        if file.endswith(".nii"):
                            return os.path.join(root, file)
            return file_path

        # Resolve paths for all required image types
        t1c_path  = resolve_file_path(patient_folder_path, patient_id + '-t1c.nii')
        t1n_path  = resolve_file_path(patient_folder_path, patient_id + '-t1n.nii')
        t2f_path  = resolve_file_path(patient_folder_path, patient_id + '-t2f.nii')
        t2w_path  = resolve_file_path(patient_folder_path, patient_id + '-t2w.nii')
        seg_path  = os.path.join(patient_folder_path, patient_id + '-seg.nii')

        t1c_loader   = loadimage( t1c_path )
        t1n_loader   = loadimage( t1n_path )
        t2f_loader   = loadimage( t2f_path )
        t2w_loader   = loadimage( t2w_path )
        masks_loader = loadimage( seg_path )

        # Make the dimension of channel
        t1c_tensor   = torch.Tensor(t1c_loader).unsqueeze(0)
        t1n_tensor   = torch.Tensor(t1n_loader).unsqueeze(0)
        t2f_tensor   = torch.Tensor(t2f_loader).unsqueeze(0)
        t2w_tensor   = torch.Tensor(t2w_loader).unsqueeze(0)
        masks_tensor = torch.Tensor(masks_loader).unsqueeze(0)

        concat_tensor = torch.cat( (t1c_tensor, t1n_tensor, t2f_tensor, t2w_tensor, masks_tensor), 0 )
        data = {            
            'imgs'  : np.array(concat_tensor[0:4,:,:,:]),
            'masks' : np.array(concat_tensor[4:,:,:,:])
        }

        augmented_imgs_masks = self.preprocess(data, self.mode)
        imgs  = np.array(augmented_imgs_masks['imgs'])
        masks = np.array(augmented_imgs_masks['masks'])

        y = {

            'imgs'  : torch.from_numpy(imgs).type(torch.FloatTensor),
            'masks' : torch.from_numpy(masks).type(torch.FloatTensor),
            'patient_id' : patient_id,
            'data_type' : data_type

        }

        return y

# Data Loaders

In [3]:
def combine_datasets(dataset_lists, batch_size):
    combined_paths = []
    num_datasets = len(dataset_lists)
    dataset_lengths = [len(dataset) for dataset in dataset_lists]
    dataset_indices = [0] * num_datasets  # Track indices for each dataset
    
    while any(idx < dataset_lengths[i] for i, idx in enumerate(dataset_indices)):
        for i in range(num_datasets):
            start_idx = dataset_indices[i]
            end_idx = min(start_idx + batch_size, dataset_lengths[i])
            batch = dataset_lists[i][start_idx:end_idx]
            combined_paths.extend(batch)
            dataset_indices[i] += batch_size
    
    return combined_paths

In [4]:
def prepare_data_loaders(args):
    train_datasets, val_datasets, test_datasets = [], [], []
    split_ratio = {'training': 0.71, 'validation': 0.09, 'testing': 0.2}
    
    for i, data_dir in enumerate(args['data_dirs']):
        patient_lists = os.listdir( data_dir )
        patient_lists.sort()
        total_patients = len(patient_lists)
        
        random.seed(5)
        random.shuffle(patient_lists)
    
        train_split = int(split_ratio['training'] * total_patients)
        val_split = int(split_ratio['validation'] * total_patients)
    
        train_patient_lists = patient_lists[:train_split]
        val_patient_lists = patient_lists[train_split : train_split + val_split]
        test_patient_lists = patient_lists[train_split + val_split :]
    
        train_patient_lists.sort()
        val_patient_lists.sort()
        test_patient_lists.sort()
        
        print(f'Number of training samples in {data_dir.split("/")[3]} DataSet: {len(train_patient_lists)}')
        print(f'Number of validation samples in {data_dir.split("/")[3]} DataSet: {len(val_patient_lists)}')
        print(f'Number of testing samples in {data_dir.split("/")[3]} DataSet: {len(test_patient_lists)} ')

        train_datasets.append(train_patient_lists)
        val_datasets.append(val_patient_lists)
        test_datasets.append(test_patient_lists)
            
    combined_trainDataset = combine_datasets(train_datasets, batch_size=args['train_batch_size'])
    combined_valDataset = list(chain.from_iterable(val_datasets))
    combined_testDataset = list(chain.from_iterable(test_datasets))
    
    print(f'Number of combined training samples', len(combined_trainDataset))
    print(f'Number of combined validation samples', len(combined_valDataset))
    print(f'Number of combined testing samples', len(combined_testDataset))
    
    trainDataset = CustomDataset3D( args['data_dirs'], combined_trainDataset, mode='training')
    valDataset = CustomDataset3D( args['data_dirs'], combined_valDataset, mode='validation')
    testDataset = CustomDataset3D( args['data_dirs'], combined_testDataset, mode='testing')
    
    trainLoader = DataLoader(
        trainDataset, batch_size=args['train_batch_size'], num_workers=args['workers'], prefetch_factor=2,
        pin_memory=True, shuffle=False)
    
    valLoader = DataLoader(
        valDataset, batch_size=args['val_batch_size'], num_workers=args['workers'], prefetch_factor=2,
        pin_memory=True, shuffle=False)
    
    testLoader = DataLoader(
        testDataset, batch_size=args['test_batch_size'], num_workers=args['workers'], prefetch_factor=2,
        pin_memory=True, shuffle=False)

    return trainLoader, valLoader, testLoader

In [5]:
# args = {
#     'workers': 2,
#     'epochs': 5,
#     'train_batch_size': 2,
#     'val_batch_size': 2,
#     'test_batch_size': 3,
#     'learning_rate': 1e-3,
#     'weight_decay': 1e-5,
#     'lambd': 0.0051,
#     'data_dirs': ["/kaggle/input/bratsglioma/Training/", "/kaggle/input/bratsafrica24/", "/kaggle/input/bratsped/Training/", "/kaggle/input/bratsmen/", "/kaggle/input/bratsmet24/"],
#     'in_checkpoint_dir': Path('/kaggle/input/f-tumors-kl-bce/'),
#     'out_checkpoint_dir': Path('/kaggle/working/')
# }

# trainLoader, valLoader, testLoader = prepare_data_loaders(args)
# for y in trainLoader:
#     print(y['data_type'])
#     print(y['patient_id'])
#     print('----------')

# Visualizing Data

In [6]:
# args = {
#     'workers': 2,
#     'epochs': 10,
#     'train_batch_size': 2,
#     'val_batch_size': 2,
#     'test_batch_size': 2,
#     'learning_rate': 1e-3,
#     'weight_decay': 1e-5,
#     'lambd': 0.0051,
#     'data_dir': '/kaggle/input/bratsafrica24/',
#     'in_checkpoint_dir': Path('/kaggle/input/adultgliomamodel-45epochs'),
#     'out_checkpoint_dir': Path('/kaggle/working/')
# }

# trainLoader, valLoader, testLoader = prepare_data_loaders(args)

# for step, y in enumerate( trainLoader ):
#   print(y['imgs'].shape)
#   print(y['patient_id'])

#   fig, axes = plt.subplots(1, 4, figsize=(16, 4))
#   for sequence in range(4):
#     sequence_data = y['imgs'][0][sequence, :, :, :].cpu().detach().numpy()
#     slice_index = sequence_data.shape[2] // 2
#     axes[sequence].imshow(np.rot90(sequence_data[:, :, slice_index]), cmap='gray', origin='lower')
#     axes[sequence].set_title(f'Sequence {sequence + 1}')

#   plt.show()

# DynUNet Model

In [7]:
class UnetBasicBlock(nn.Module):
    """
    A CNN module module that can be used for DynUNet, based on:
    `Automated Design of Deep Learning Methods for Biomedical Image Segmentation <https://arxiv.org/abs/1904.08128>`_.
    `nnU-Net: Self-adapting Framework for U-Net-Based Medical Image Segmentation <https://arxiv.org/abs/1809.10486>`_.

    Args:
        spatial_dims: number of spatial dimensions.
        in_channels: number of input channels.
        out_channels: number of output channels.
        kernel_size: convolution kernel size.
        stride: convolution stride.
        norm_name: feature normalization type and arguments.
        act_name: activation layer type and arguments.
        dropout: dropout probability.

    """

    def __init__(
        self,
        spatial_dims: int,
        in_channels: int,
        out_channels: int,
        kernel_size: Union[Sequence[int], int],
        stride: Union[Sequence[int], int],
        norm_name: Union[Tuple, str] = ("INSTANCE", {"affine": True}),
        act_name: Union[Tuple, str] = ("leakyrelu", {"inplace": True, "negative_slope": 0.01}),
        dropout: Optional[Union[Tuple, str, float]] = None,
    ):
        super().__init__()
        self.conv1 = get_conv_layer(
            spatial_dims,
            in_channels,
            out_channels,
            kernel_size=kernel_size,
            stride=stride,
            dropout=dropout,
            conv_only=True,
        )

        self.conv2 = get_conv_layer(
            spatial_dims,
            out_channels,
            out_channels,
            kernel_size=kernel_size,
            stride=1,
            dropout=dropout,
            conv_only=True
        )
        self.lrelu = get_act_layer(name=act_name)
        self.norm1 = get_norm_layer(name=norm_name, spatial_dims=spatial_dims, channels=out_channels)
        self.norm2 = get_norm_layer(name=norm_name, spatial_dims=spatial_dims, channels=out_channels)

    def forward(self, inp):
        out = self.conv1(inp)
        out = self.norm1(out)
        out = self.lrelu(out)
        out = self.conv2(out)
        out = self.norm2(out)
        out = self.lrelu(out)
        return out



class UnetUpBlock(nn.Module):
    """
    An upsampling module that can be used for DynUNet, based on:
    `Automated Design of Deep Learning Methods for Biomedical Image Segmentation <https://arxiv.org/abs/1904.08128>`_.
    `nnU-Net: Self-adapting Framework for U-Net-Based Medical Image Segmentation <https://arxiv.org/abs/1809.10486>`_.

    Args:
        spatial_dims: number of spatial dimensions.
        in_channels: number of input channels.
        out_channels: number of output channels.
        kernel_size: convolution kernel size.
        stride: convolution stride.
        upsample_kernel_size: convolution kernel size for transposed convolution layers.
        norm_name: feature normalization type and arguments.
        act_name: activation layer type and arguments.
        dropout: dropout probability.
        trans_bias: transposed convolution bias.

    """

    def __init__(
        self,
        spatial_dims: int,
        in_channels: int,
        out_channels: int,
        kernel_size: Union[Sequence[int], int],
        upsample_kernel_size: Union[Sequence[int], int],
        norm_name: Union[Tuple, str] = ("INSTANCE", {"affine": True}),
        act_name: Union[Tuple, str] = ("leakyrelu", {"inplace": True, "negative_slope": 0.01}),
        dropout: Optional[Union[Tuple, str, float]] = None,
        trans_bias: bool = False,
    ):
        super().__init__()
        upsample_stride = upsample_kernel_size
        
        # ( a purple arrow in the paper )
        self.transp_conv = get_conv_layer(
            spatial_dims,
            in_channels,
            out_channels,
            kernel_size=upsample_kernel_size,
            stride=upsample_stride,
            dropout=dropout,
            bias=trans_bias,
            conv_only=True,
            is_transposed=True,
        )
        
        # A light blue conv blocks in the decoder of nnUNet
        self.conv_block = UnetBasicBlock(
            spatial_dims,
            out_channels + out_channels,
            out_channels,
            kernel_size=kernel_size,
            stride=1,
            dropout=dropout,
            norm_name=norm_name,
            act_name=act_name,
        )

    def forward(self, inp, skip):
        # number of channels for skip should equals to out_channels
        out = self.transp_conv(inp)
        out = torch.cat((out, skip), dim=1)
        out = self.conv_block(out)
        return out



class UnetOutBlock(nn.Module):
    def __init__(
        self, spatial_dims: int, in_channels: int, out_channels: int, dropout: Optional[Union[Tuple, str, float]] = None
    ):
        super().__init__()
        self.conv = get_conv_layer(
            spatial_dims, in_channels, out_channels, kernel_size=1, stride=1, dropout=dropout, bias=True, conv_only=True
        )

    def forward(self, inp):
        return self.conv(inp)
    

def get_conv_layer(
    spatial_dims: int,
    in_channels: int,
    out_channels: int,
    kernel_size: Union[Sequence[int], int] = 3,
    stride: Union[Sequence[int], int] = 1,
    act: Optional[Union[Tuple, str]] = Act.PRELU,
    norm: Union[Tuple, str] = Norm.INSTANCE,
    dropout: Optional[Union[Tuple, str, float]] = None,
    bias: bool = False,
    conv_only: bool = True,
    is_transposed: bool = False,
):
    padding = get_padding(kernel_size, stride)
    output_padding = None
    if is_transposed:
        output_padding = get_output_padding(kernel_size, stride, padding)
    
    return Convolution(
        spatial_dims,
        in_channels,
        out_channels,
        strides=stride,
        kernel_size=kernel_size,
        act=act,
        norm=norm,
        dropout=dropout,
        bias=bias,
        conv_only=conv_only,
        is_transposed=is_transposed,
        padding=padding,
        output_padding=output_padding,
    )


def get_padding(
    kernel_size: Union[Sequence[int], int], stride: Union[Sequence[int], int]
) -> Union[Tuple[int, ...], int]:

    kernel_size_np = np.atleast_1d(kernel_size)
    stride_np = np.atleast_1d(stride)
    padding_np = (kernel_size_np - stride_np + 1) / 2
    if np.min(padding_np) < 0:
        raise AssertionError("padding value should not be negative, please change the kernel size and/or stride.")
    padding = tuple(int(p) for p in padding_np)

    return padding if len(padding) > 1 else padding[0]


def get_output_padding(
    kernel_size: Union[Sequence[int], int], stride: Union[Sequence[int], int], padding: Union[Sequence[int], int]
) -> Union[Tuple[int, ...], int]:
    kernel_size_np = np.atleast_1d(kernel_size)
    stride_np = np.atleast_1d(stride)
    padding_np = np.atleast_1d(padding)

    out_padding_np = 2 * padding_np + stride_np - kernel_size_np
    if np.min(out_padding_np) < 0:
        raise AssertionError("out_padding value should not be negative, please change the kernel size and/or stride.")
    out_padding = tuple(int(p) for p in out_padding_np)

    return out_padding if len(out_padding) > 1 else out_padding[0]

def set_requires_grad(nets, requires_grad=False):
    if not isinstance(nets, list):
        nets = [nets]
    for net in nets:
        if net is not None:
            for param in net.parameters():
                param.requires_grad = requires_grad

In [8]:
class DynUNet(nn.Module):
    def __init__(
        self,
        spatial_dims: int,
        in_channels: int,
        out_channels: int,
        deep_supervision: bool,
        KD: bool = False
    ):
        super().__init__()
        self.spatial_dims = spatial_dims
        self.in_channels = in_channels
        self.out_channels = out_channels
        self.deep_supervision = deep_supervision
        self.KD_enabled = KD
        
        self.input_conv = UnetBasicBlock( spatial_dims=self.spatial_dims,
                                     in_channels=self.in_channels,
                                     out_channels=64,
                                     kernel_size=3,
                                     stride=1
                                     )
        self.down1 = UnetBasicBlock( spatial_dims=self.spatial_dims,
                                     in_channels=64,
                                     out_channels=96,
                                     kernel_size=3,
                                     stride=2 # Reduces spatial dims by 2
                                     )
        self.down2 = UnetBasicBlock( spatial_dims=self.spatial_dims,
                                     in_channels=96,
                                     out_channels=128,
                                     kernel_size=3,
                                     stride=2
                                     )
        self.down3 = UnetBasicBlock( spatial_dims=self.spatial_dims,
                                     in_channels=128,
                                     out_channels=192,
                                     kernel_size=3,
                                     stride=2
                                     )
        self.down4 = UnetBasicBlock( spatial_dims=self.spatial_dims,
                                     in_channels=192,
                                     out_channels=256,
                                     kernel_size=3,
                                     stride=2
                                     )
        self.down5 = UnetBasicBlock( spatial_dims=self.spatial_dims,
                                     in_channels=256,
                                     out_channels=384,
                                     kernel_size=3,
                                     stride=2
                                     )
        self.bottleneck = UnetBasicBlock( spatial_dims=self.spatial_dims,
                                     in_channels=384,
                                     out_channels=512,
                                     kernel_size=3,
                                     stride=2
                                     )
        self.up1 = UnetUpBlock( spatial_dims=self.spatial_dims,
                                in_channels=512,
                                out_channels=384,
                                kernel_size=3,
                                upsample_kernel_size=2
                                )
        self.up2 = UnetUpBlock( spatial_dims=self.spatial_dims,
                                in_channels=384,
                                out_channels=256,
                                kernel_size=3,
                                upsample_kernel_size=2
                                )
        self.up3 = UnetUpBlock( spatial_dims=self.spatial_dims,
                                in_channels=256,
                                out_channels=192,
                                kernel_size=3,
                                upsample_kernel_size=2
                                )
        self.up4 = UnetUpBlock( spatial_dims=self.spatial_dims,
                                in_channels=192,
                                out_channels=128,
                                kernel_size=3,
                                upsample_kernel_size=2
                                )
        
        self.up5 = UnetUpBlock( spatial_dims=self.spatial_dims,
                                in_channels=128,
                                out_channels=96,
                                kernel_size=3,
                                upsample_kernel_size=2
                                )        
        self.up6 = UnetUpBlock( spatial_dims=self.spatial_dims,
                                in_channels=96,
                                out_channels=64,
                                kernel_size=3,
                                upsample_kernel_size=2
                                )
        self.out1 = UnetOutBlock( spatial_dims=self.spatial_dims,
                                  in_channels=64,
                                  out_channels=self.out_channels,
                                  )
        self.out2 = UnetOutBlock( spatial_dims=self.spatial_dims,
                                  in_channels=96,
                                  out_channels=self.out_channels,
                                  )
        self.out3 = UnetOutBlock( spatial_dims=self.spatial_dims,
                                  in_channels=128,
                                  out_channels=self.out_channels,
                                  )
        
    def forward( self, input ):
        
        # Input
        x0 = self.input_conv( input ) # x0.shape = (B x 64 x 128 x 128 x 128)
        
        # Encoder
        x1 = self.down1( x0 ) # x1.shape = (B x 96 x 64 x 64 x 64) 
        x2 = self.down2( x1 ) # x2.shape = (B x 128 x 32 x 32 x 32)
        x3 = self.down3( x2 ) # x3.shape = (B x 192 x 16 x 16 x 16)
        x4 = self.down4( x3 ) # x4.shape = (B x 256 x 8 x 8 x 8)   
        x5 = self.down5( x4 ) # x5.shape = (B x 384 x 4 x 4 x 4)   
        
        # Bottleneck
        x6 = self.bottleneck( x5 ) # x6.shape = (B x 512 x 2 x 2 x 2)
        
        # Decoder
        x7  = self.up1( x6, x5 )  # x7.shape  = (B x 384 x 4 x 4 x 4)
        x8  = self.up2( x7, x4 )  # x8.shape  = (B x 256 x 8 x 8 x 8)
        x9  = self.up3( x8, x3 )  # x9.shape  = (B x 192 x 16 x 16 x 16)
        x10 = self.up4( x9, x2 )  # x10.shape = (B x 128 x 32 x 32 x 32)
        x11 = self.up5( x10, x1 ) # x11.shape = (B x 96 x 64 x 64 x 64)
        x12 = self.up6( x11, x0 ) # x12.shape = (B x 64 x 128 x 128 x 128)
        
        # Output
        output1 = self.out1( x12 )
        
        if (self.training and self.deep_supervision) or self.KD_enabled:
            
            # output['pred'].shape = B x 3 x 4 x 128 x 128 x 128
            output2 = interpolate( self.out2( x11 ), output1.shape[2:])
            output3 = interpolate( self.out3( x10 ), output1.shape[2:])
            output_all = [ output1, output2, output3 ]
            return { 'pred' : torch.stack(output_all, dim=1),
                     'bottleneck_feature_map' : x6 }
        
        return { 'pred' : output1 }

# Visualizing Model Instance

In [9]:
# !pip install torchsummary
# from torchsummary import summary

# # Initialize your DynUNet model
# model = DynUNet(spatial_dims=3, in_channels=4, out_channels=4, deep_supervision=True, KD=True)

# # Print model summary
# summary(model, input_size=(4, 128, 128, 128))  # Adjust input_size according to your needs

# ClearML

In [10]:
!pip install clearml
from clearml import Task

%env CLEARML_WEB_HOST=https://app.clear.ml/
%env CLEARML_API_HOST=https://api.clear.ml
%env CLEARML_FILES_HOST=https://files.clear.ml
%env CLEARML_API_ACCESS_KEY=CLEARML_API_ACCESS_KEY
%env CLEARML_API_SECRET_KEY=CLEARML_API_SECRET_KEY

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 18.3 MB/s eta 0:00:00
env: CLEARML_WEB_HOST=https://app.clear.ml/
env: CLEARML_API_HOST=https://api.clear.ml
env: CLEARML_FILES_HOST=https://files.clear.ml
env: CLEARML_API_ACCESS_KEY=ZQ1VS50L15BU5QDS1SCI5J01C35V11
env: CLEARML_API_SECRET_KEY=vCt1vMmo1WdBrY6biEgH7b4DksznnHjyYcZp3o2y0sJBo9mS27LhScPhVZoaZj6NdOM


# GPUs Check

In [11]:
if torch.cuda.is_available():
    num_gpus = torch.cuda.device_count()
    print(f"Number of GPUs available: {num_gpus}")
    for i in range(num_gpus):
        print(f"GPU {i}: {torch.cuda.get_device_name(i)}")
else:
    print("No GPU available. Running on CPU.")

Number of GPUs available: 2
GPU 0: Tesla T4
GPU 1: Tesla T4


In [12]:
# # For freeing gpu
# import gc; gc.collect(); torch.cuda.empty_cache()

# Loss Function

In [13]:
class LossFunction(nn.Module):
    def __init__(self):
        super(LossFunction, self).__init__()
        self.dice = DiceLoss(sigmoid=True, batch=True, smooth_nr=1e-05, smooth_dr=1e-05)
        self.ce = nn.BCEWithLogitsLoss()

    def _loss(self, p, y):
        return self.dice(p, y) + self.ce(p, y.float())

    def forward(self, p, y):
        y_wt, y_tc, y_et = y > 0, ((y == 1) + (y == 3)) > 0, y == 3
        p_wt, p_tc, p_et = p[:, 1].unsqueeze(1), p[:, 2].unsqueeze(1), p[:, 3].unsqueeze(1)
        l_wt, l_tc, l_et = self._loss(p_wt, y_wt), self._loss(p_tc, y_tc), self._loss(p_et, y_et)
        return l_wt + l_tc + l_et

# Student KD Model

In [14]:
class CBAMFeatureExtractor(nn.Module):
    def __init__(self, in_channels, reduction=16, kernel_size=7):
        super(CBAMFeatureExtractor, self).__init__()

        # Channel Attention
        self.avg_pool = nn.AdaptiveAvgPool3d(1)
        self.max_pool = nn.AdaptiveMaxPool3d(1)
        self.fc = nn.Sequential(
            nn.Conv3d(in_channels, in_channels // reduction, 1, bias=False),
            nn.ReLU(),
            nn.Conv3d(in_channels // reduction, in_channels, 1, bias=False),
            nn.Sigmoid()
        )

        # Spatial Attention
        self.conv = nn.Conv3d(2, 1, kernel_size, padding=kernel_size//2, bias=False)
        self.sigmoid = nn.Sigmoid()

    def forward(self, x):
        """ Extracts attention-enhanced feature maps """

        # Channel Attention
        avg_out = self.fc(self.avg_pool(x))
        max_out = self.fc(self.max_pool(x))
        channel_attention = avg_out + max_out
        x = x * channel_attention  # Apply channel attention

        # Spatial Attention
        avg_out = torch.mean(x, dim=1, keepdim=True)
        max_out, _ = torch.max(x, dim=1, keepdim=True)
        spatial_attention = self.sigmoid(self.conv(torch.cat([avg_out, max_out], dim=1)))
        x = x * spatial_attention  # Apply spatial attention

        return x  # Return enhanced features

In [15]:
class Student_KD_loss(nn.Module):
    def __init__(self):
        super().__init__()
        self.student = DynUNet( spatial_dims=3, in_channels=4, out_channels=4, deep_supervision=True)
        self.loss_fn = LossFunction()
        self.temperature = 5.0
        self.bce_loss = nn.BCEWithLogitsLoss()
        self.cbam_extractor = CBAMFeatureExtractor(in_channels=512)
        
    def forward(self, teacher_outputs, y):
        with amp.autocast('cuda:1'):
            student_outputs = self.student( y['imgs'] )

            # Student loss with Deep supervision -> (Dice loss)            
            segloss_s_decoder_1 = self.loss_fn( student_outputs['pred'][:,0], y['masks'] ) # student_outputs['pred'].shape = B x 3 x 4 x 128 x 128 x 128
            segloss_s_decoder_2 = self.loss_fn( student_outputs['pred'][:,1], y['masks'] )
            segloss_s_decoder_3 = self.loss_fn( student_outputs['pred'][:,2], y['masks'] )

            student_seg_loss = segloss_s_decoder_1 + 0.5*segloss_s_decoder_2 + 0.25*segloss_s_decoder_3

            #-----------------------------------------------------------------------------------#
            
            # KD loss between bottleneck layers -> (KL with CBAM Loss)
            teacher_bottleneck = teacher_outputs['bottleneck_feature_map']
            student_bottleneck = student_outputs['bottleneck_feature_map']
            
            # Extract attention-enhanced features from bottleneck
            teacher_bottleneck_att = self.cbam_extractor(teacher_bottleneck)  # (B, 512, 8)
            student_bottleneck_att = self.cbam_extractor(student_bottleneck)  # (B, 512, 8)
            
            # Normalize to probability distributions
            student_probs = F.log_softmax(student_bottleneck_att, dim=1)  # Log probabilities
            teacher_probs = F.softmax(teacher_bottleneck_att, dim=1)      # Probabilities
            
            # Compute KL loss instead of MSE
            kl_loss_with_teacher = F.kl_div(student_probs, teacher_probs, reduction='batchmean')

            #-----------------------------------------------------------------------------------#

            # KD loss between prediction layers -> (BCE Loss on logits with DS)
            bce_loss_with_teacher = 0
            decoder_weights = [1, 0.5, 0.25]

            for decoder_idx, weight in enumerate(decoder_weights):
                teacher_logits = teacher_outputs['pred'][:, decoder_idx] / self.temperature  # Shape: (B, 4, 128, 128, 128)
                student_logits = student_outputs['pred'][:, decoder_idx] / self.temperature  # Shape: (B, 4, 128, 128, 128)
                
                # Compute hard labels for WT, TC, ET
                teacher_probs = torch.sigmoid(teacher_logits)
                teacher_hard_labels = [
                    (teacher_probs[:, channel_idx] > 0.5).float().unsqueeze(1) for channel_idx in range(1, 4)
                ]
                
                # Extract student logits for WT, TC, ET
                student_logits_channels = [
                    student_logits[:, channel_idx].unsqueeze(1) for channel_idx in range(1, 4)
                ]
                
                # Compute BCE losses for WT, TC, ET
                bce_losses = [
                    self.bce_loss(student_logits_channels[i], teacher_hard_labels[i]) for i in range(3)
                ]
                
                # Aggregate loss for this decoder with the corresponding weight
                bce_loss_with_teacher += sum(bce_losses) * (self.temperature ** 2) * weight
            
            #-----------------------------------------------------------------------------------#

            beta, alpha, gamma, zeta = 10, 1.0, 0.0006, 0.1

            print("Seg loss: ", student_seg_loss)
            print("KL loss with teacher: ", kl_loss_with_teacher)
            # print("Cosine loss with teacher: ", cosine_loss_with_teacher)
            print("BCE loss with teacher: ", bce_loss_with_teacher)

            print("Seg loss weighted: ", alpha*student_seg_loss)
            print("KL loss with teacher weighted: ", beta*kl_loss_with_teacher)
            # print("Cosine loss with teacher weighted: ", gamma*cosine_loss_with_teacher)
            print("BCE loss with teacher weighted: ", zeta*bce_loss_with_teacher)

            # batch_total_student_loss = alpha*student_seg_loss + beta*kl_loss_with_teacher + gamma*cosine_loss_with_teacher + zeta*bce_loss_with_teacher
            batch_total_student_loss = alpha*student_seg_loss + beta*kl_loss_with_teacher + zeta*bce_loss_with_teacher
            
            print("-------------Final student loss-------------")
            print(batch_total_student_loss)
            print("-------------Final student loss-------------")

        KD_output = {
            'batch_total_student_loss' : batch_total_student_loss,
            'seg_weighted'   : alpha*student_seg_loss,
            'kl_weighted'    : beta*kl_loss_with_teacher,
            'bce_weighted'   : zeta*bce_loss_with_teacher,
            # 'cos_weighted'   : gamma*cosine_loss_with_teacher
        }
            
        return KD_output

# Training & Validation

In [16]:
def evaluate(model, loader, epoch, task):
    torch.manual_seed(0)
    model.eval()
    loss_fn = LossFunction()
    n_val_batches = len(loader)
    
    tumors_val_losses, running_loss = validate_model(model, loader, loss_fn)
    epoch_val_loss = running_loss / n_val_batches
    log_val_epoch_losses(tumors_val_losses, epoch, task, epoch_val_loss)
    
    print(f"------Final validation dice loss after epoch {epoch + 1}: {epoch_val_loss}-------")
    
    model.student.to('cuda:1')
    model.train()
    
    return epoch_val_loss

def validate_model(model, loader, loss_fn):
    tumors_val_losses = {'GLI': [], 'PED': [], 'SSA': [], 'MEN': [], 'MET': []}
    running_loss = 0
    n_val_batches = len(loader)
    
    with tqdm(total=n_val_batches, desc='Validating', unit='batch', leave=False) as pbar:
        with torch.no_grad():
            for y in loader:
                val_loss, data_type = process_batch(model, y, loss_fn)
                tumors_val_losses[data_type].append(val_loss.item())
                running_loss += val_loss
                pbar.update(1)
    
    return tumors_val_losses, running_loss

def process_batch(model, y, loss_fn):
    y['imgs'], y['masks'] = y['imgs'].to('cuda'), y['masks'].to('cuda')
    data_type = y['data_type'][0]
    
    with torch.amp.autocast('cuda'):
        output = model.student.to('cuda')(y['imgs'])
        val_loss = loss_fn(output['pred'], y['masks'])
        
    print(f"Validation dice loss per batch: {val_loss}")
    return val_loss, data_type

def log_val_epoch_losses(tumors_val_losses, epoch, task, epoch_val_loss):
    for tumor_type, losses in tumors_val_losses.items():
        avg_loss = sum(losses) / len(losses) if losses else 0
        task.get_logger().report_scalar(
            title=f"{tumor_type} Losses over Epochs",
            series=f"{tumor_type} Epoch valLoss",
            iteration=epoch + 1,
            value=avg_loss
        )

    task.get_logger().report_scalar("KD Losses over Epochs", "val_loss", iteration=epoch+1, value=epoch_val_loss)

In [17]:
def setup_environment(args):
    torch.manual_seed(0)
    args['out_checkpoint_dir'].mkdir(parents=True, exist_ok=True)

def initialize_models():
    teacher_model = DynUNet(spatial_dims=3, in_channels=4, out_channels=4, deep_supervision=True, KD=True).to('cuda:0')
    student_model = Student_KD_loss().to('cuda:1')
    return teacher_model, student_model

def initialize_optimizer_scheduler(student_model, args):
    optimizer = optim.AdamW(student_model.parameters(), lr=args['learning_rate'], weight_decay=args['weight_decay'], eps=1e-4)
    scheduler = optim.lr_scheduler.ReduceLROnPlateau(optimizer, mode='min', factor=0.1, patience=10, cooldown=1, threshold=0.001, min_lr=1e-6)
    return optimizer, scheduler

def load_teacher_model(teacher_model, data_type, teacher_model_paths):
    teacher_model_path = teacher_model_paths.get(data_type)
    if teacher_model_path and Path(teacher_model_path).is_file():
        ckpt = torch.load(teacher_model_path, map_location='cuda:0', weights_only=True)
        teacher_model.load_state_dict(ckpt['teacher_model'])
        print(f"Loaded model: {teacher_model_path}")

def load_student_checkpoint(student_model, optimizer, scaler, scheduler, args):
    checkpoint_path = args['in_checkpoint_dir'] / 'Student_model_after_epoch_126_trainLoss_0.7168_valLoss_0.4047.pth'
    if checkpoint_path.is_file():
        print(f"Found model {checkpoint_path}")
        ckpt = torch.load(checkpoint_path, map_location='cuda:1', weights_only=True)
        student_model.student.load_state_dict(ckpt['student_model'])
        optimizer.load_state_dict(ckpt['optimizer_student'])
        scaler.load_state_dict(ckpt['grad_scaler_state'])
        scheduler.load_state_dict(ckpt['scheduler_state_dict'])
        print(f"Loaded student model: {checkpoint_path} with lr: {optimizer.param_groups[0]['lr']}")
        return ckpt['epoch'] + 1
    return 0

def train_epoch(epoch, trainLoader, train_config, start_ep):
    student_model = train_config['student_model']
    teacher_model = train_config['teacher_model']
    optimizer = train_config['optimizer']
    scaler = train_config['scaler']
    teacher_model_paths = train_config['teacher_model_paths']
    task = train_config['task']
    
    student_model.train()
    teacher_model.eval()
    
    epoch_losses = {'total': 0, 'kl': 0, 'seg': 0, 'bce': 0}
    tumors_losses = {'GLI': [], 'SSA': [], 'PED': [], 'MEN': [], 'MET': []}
    
    with tqdm(total=len(trainLoader), desc=f"(Epoch {epoch + 1}/{start_ep + train_config['epochs']})", unit='batch') as pbar:
        optimizer.zero_grad()
        for step, y in enumerate(trainLoader):
            print('Patient ids: ', y['patient_id'])
            print('Population: ', y['data_type'])
            data_type = y['data_type'][0]
            
            optimizer.zero_grad()
            imgs, masks = y['imgs'].to('cuda:0'), y['masks'].to('cuda:0')
            load_teacher_model(teacher_model, data_type, teacher_model_paths)
            
            with amp.autocast('cuda:0'):
                teacher_outputs = teacher_model(imgs)
                
            detached_teacher_output = {k: v.detach().to('cuda:1') for k, v in teacher_outputs.items()}
            imgs, masks = imgs.to('cuda:1'), masks.to('cuda:1')
                
            with amp.autocast('cuda:1'):
                student_outputs = student_model(detached_teacher_output, {'imgs': imgs, 'masks': masks})
                loss = student_outputs['batch_total_student_loss']
                tumors_losses[data_type].append(loss.item())
                
            scaler.scale(loss).backward()
            scaler.step(optimizer)
            scaler.update()

            task.get_logger().report_scalar(
                title=f"Tumors training losses per epoch {epoch+1}",
                series=f"{data_type} loss",
                iteration=len(tumors_losses[data_type]),
                value=float(loss.item())
            )
            
            for key in epoch_losses:
                if key != 'total':
                    epoch_losses[key] += student_outputs.get(f'{key}_weighted', 0)
                else:
                    epoch_losses['total'] += loss.item() 
                            
            pbar.update(1)
    
        for key in epoch_losses:
            epoch_losses[key] /= len(trainLoader)
        
    return epoch_losses, tumors_losses

def log_KD_losses_over_epochs(epoch, epoch_losses, tumors_losses, task):
    for loss_type, val in epoch_losses.items():
        task.get_logger().report_scalar(
            title="KD Losses over Epochs",
            series=f"{loss_type} loss",
            iteration=epoch + 1,
            value=epoch_losses[loss_type]
        )    

    for tumor_type, losses in tumors_losses.items():
        task.get_logger().report_scalar(
            title=f"{tumor_type} Losses over Epochs",
            series=f"{tumor_type} Epoch trainLoss",
            iteration=epoch + 1,
            value=sum(losses) / len(losses) if losses else 0
        )

def validate_and_save(epoch, valLoader, train_config, epoch_losses):
    student_model = train_config['student_model']
    scheduler = train_config['scheduler']
    optimizer = train_config['optimizer']
    scaler = train_config['scaler']
    out_checkpoint_dir = train_config['out_checkpoint_dir']
    task = train_config['task']

    val_loss = evaluate(student_model, valLoader, epoch, task)
    scheduler.step(val_loss)

    task.get_logger().report_scalar("LR", "learning_rate", iteration=epoch+1, value=optimizer.param_groups[0]['lr'])
    print(f"Learning rate after epoch {epoch + 1}: {optimizer.param_groups[0]['lr']}")

    # if(epoch + 1) % 5 == 0:
    state = {
        'epoch': epoch,
        'student_model': student_model.student.state_dict(),
        'optimizer_student': optimizer.state_dict(),
        'lr': optimizer.param_groups[0]['lr'],
        'grad_scaler_state': scaler.state_dict(),
        'scheduler_state_dict': scheduler.state_dict(),
        'val_dice_loss': val_loss
    }

    checkpoint_path = out_checkpoint_dir / f'Student_model_after_epoch_{epoch + 1}_trainLoss_{epoch_losses["total"]:.4f}_valLoss_{val_loss:.4f}.pth'
    torch.save(state, checkpoint_path)
    print(f"Model saved after epoch {epoch + 1}")

def run_KD(trainLoader, valLoader, args):
    setup_environment(args)
    teacher_model, student_model = initialize_models()
    optimizer, scheduler = initialize_optimizer_scheduler(student_model, args)
    scaler = amp.GradScaler('cuda:1')
    
    teacher_model_paths = {
        'GLI': '/kaggle/input/gliomateachernewlabels/Teacher_model_after_epoch_100_trainLoss_0.5972_valLoss_0.3019.pth',
        'SSA': '/kaggle/input/africanewlabels/Teacher_model_after_epoch_67_trainLoss_1.1080_valLoss_0.5561.pth',
        'PED': '/kaggle/input/pednewlabel/Teacher_model_after_epoch_99_trainLoss_1.4512_valLoss_1.0042.pth',
        'MEN': '/kaggle/input/meningiomateachernewlabels/Teacher_model_after_epoch_85_trainLoss_0.5824_valLoss_0.3318.pth',
        'MET': '/kaggle/input/met-teacher-new-labels/Teacher_model_after_epoch_100_trainLoss_1.6278_valLoss_0.7199.pth'
    }
    
    start_epoch = load_student_checkpoint(student_model, optimizer, scaler, scheduler, args)

    print(f"Initial learning rate after loading checkpoint: {optimizer.param_groups[0]['lr']}")

    # new_learning_rate = 2e-4
    # for param_group in optimizer.param_groups:
    #     param_group['lr'] = new_learning_rate
    # print(f"Updated learning rate: {new_learning_rate}")

    new_min_lr = 1e-6
    scheduler = optim.lr_scheduler.ReduceLROnPlateau(optimizer, mode='min', factor=0.1, patience=10, cooldown=1, threshold=0.001, min_lr=new_min_lr)
    print(f"Updated min_lr: {new_min_lr}")

    task = Task.init(project_name="CASED(des) KD 5 Tumors Original Teachers", task_name=f" CASED 5 Tumors Descending Experiment 132ep", reuse_last_task_id=True)
    task.connect(args)
    task.add_tags(['CBAM(KL)+BCE+SEG', "nourhanahmed285"])

    print(f'''Starting Knowledge Distillation:
            Epochs:          From {start_epoch + 1} to {start_epoch + args['epochs']}
            Batch size:      {args['train_batch_size']}
            Learning rate:  {args['learning_rate']}
            Training data coming from: {args['data_dirs']}
    ''')

    train_config = {
        'teacher_model': teacher_model,
        'student_model': student_model,
        'optimizer': optimizer,
        'scheduler': scheduler,
        'scaler': scaler,
        'teacher_model_paths': teacher_model_paths,
        'out_checkpoint_dir': args['out_checkpoint_dir'],
        'task': task,
        'epochs': args['epochs']
    }
    
    for epoch in range(start_epoch, start_epoch + args['epochs']):
        epoch_losses, tumors_losses = train_epoch(epoch, trainLoader, train_config, start_epoch)
        log_KD_losses_over_epochs(epoch, epoch_losses, tumors_losses, task)
        validate_and_save(epoch, valLoader, train_config, epoch_losses)
    
    print("Training completed.")
    task.close()

In [18]:
args = {
    'workers': 2,
    'epochs': 6,
    'train_batch_size': 2,
    'val_batch_size': 2,
    'test_batch_size': 3,
    'learning_rate': 1e-3,
    'weight_decay': 1e-5,
    'lambd': 0.0051,
    # 'data_dirs': ["/kaggle/input/bratsglioma/Training/", "/kaggle/input/bratsafrica24/", "/kaggle/input/bratsped/Training/", "/kaggle/input/bratsmen/", "/kaggle/input/bratsmet24/"],
    'data_dirs': ["/kaggle/input/bratsglioma/Training/", "/kaggle/input/bratsmen/", "/kaggle/input/bratsmet24/", "/kaggle/input/bratsafrica24/", "/kaggle/input/bratsped/Training/"],
    'in_checkpoint_dir': Path('/kaggle/input/cased-des-originalt-cbamkl-120ep/'),
    'out_checkpoint_dir': Path('/kaggle/working/')
}

trainLoader, valLoader, testLoader = prepare_data_loaders(args)
run_KD(trainLoader, valLoader, args)

Number of training samples in bratsglioma DataSet: 888
Number of validation samples in bratsglioma DataSet: 112
Number of testing samples in bratsglioma DataSet: 251 
Number of training samples in bratsmen DataSet: 710
Number of validation samples in bratsmen DataSet: 90
Number of testing samples in bratsmen DataSet: 200 
Number of training samples in bratsmet24 DataSet: 232
Number of validation samples in bratsmet24 DataSet: 29
Number of testing samples in bratsmet24 DataSet: 67 
Number of training samples in bratsafrica24 DataSet: 102
Number of validation samples in bratsafrica24 DataSet: 13
Number of testing samples in bratsafrica24 DataSet: 30 
Number of training samples in bratsped DataSet: 70
Number of validation samples in bratsped DataSet: 8
Number of testing samples in bratsped DataSet: 21 
Number of combined training samples 2002
Number of combined validation samples 252
Number of combined testing samples 569
Found model /kaggle/input/cased-des-originalt-cbamkl-120ep/Student_

(Epoch 127/132):   0%|          | 0/1001 [00:00<?, ?batch/s]/usr/local/lib/python3.10/dist-packages/monai/utils/deprecate_utils.py:321: FutureWarning:

monai.transforms.croppad.dictionary CropForegroundd.__init__:allow_smaller: Current default value of argument `allow_smaller=True` has been deprecated since version 1.2. It will be changed to `allow_smaller=False` in version 1.5.

/usr/local/lib/python3.10/dist-packages/monai/utils/deprecate_utils.py:321: FutureWarning:

monai.transforms.croppad.dictionary CropForegroundd.__init__:allow_smaller: Current default value of argument `allow_smaller=True` has been deprecated since version 1.2. It will be changed to `allow_smaller=False` in version 1.5.



Patient ids:  ['BraTS-GLI-00002-000', 'BraTS-GLI-00003-000']
Population:  ['GLI', 'GLI']
2025-06-12 11:12:04,662 - clearml.model - INFO - Selected model id: 8f151de73c1c4f8e93fa8f2808579c79
Loaded model: /kaggle/input/gliomateachernewlabels/Teacher_model_after_epoch_100_trainLoss_0.5972_valLoss_0.3019.pth
Seg loss:  tensor(0.6648, device='cuda:1', grad_fn=<AddBackward0>)
KL loss with teacher:  tensor(0.1705, device='cuda:1', grad_fn=<DivBackward0>)
BCE loss with teacher:  tensor(0.4593, device='cuda:1', grad_fn=<AddBackward0>)
Seg loss weighted:  tensor(0.6648, device='cuda:1', grad_fn=<MulBackward0>)
KL loss with teacher weighted:  tensor(1.7046, device='cuda:1', grad_fn=<MulBackward0>)
BCE loss with teacher weighted:  tensor(0.0459, device='cuda:1', grad_fn=<MulBackward0>)
-------------Final student loss-------------
tensor(2.4153, device='cuda:1', grad_fn=<AddBackward0>)
-------------Final student loss-------------


(Epoch 127/132):   0%|          | 1/1001 [00:20<5:43:25, 20.61s/batch]

Patient ids:  ['BraTS-MEN-00004-000', 'BraTS-MEN-00010-000']
Population:  ['MEN', 'MEN']
2025-06-12 11:12:20,626 - clearml.model - INFO - Selected model id: a5f4aa575a2f416a8404590342d93c7a
Loaded model: /kaggle/input/meningiomateachernewlabels/Teacher_model_after_epoch_85_trainLoss_0.5824_valLoss_0.3318.pth
Seg loss:  tensor(0.5669, device='cuda:1', grad_fn=<AddBackward0>)
KL loss with teacher:  tensor(0.2504, device='cuda:1', grad_fn=<DivBackward0>)
BCE loss with teacher:  tensor(0.0334, device='cuda:1', grad_fn=<AddBackward0>)
Seg loss weighted:  tensor(0.5669, device='cuda:1', grad_fn=<MulBackward0>)
KL loss with teacher weighted:  tensor(2.5041, device='cuda:1', grad_fn=<MulBackward0>)
BCE loss with teacher weighted:  tensor(0.0033, device='cuda:1', grad_fn=<MulBackward0>)
-------------Final student loss-------------
tensor(3.0744, device='cuda:1', grad_fn=<AddBackward0>)
-------------Final student loss-------------


...

Validation dice loss per batch: 0.9262464642524719


Validating:  99%|█████████▉| 125/126 [08:27<00:03,  3.37s/batch]

Validation dice loss per batch: 0.850612223148346


Validation dice loss per batch: 0.5657756328582764


------Final validation dice loss after epoch 132: 0.38736578822135925-------
Learning rate after epoch 132: 0.0002
Model saved after epoch 132
Training completed.


# Testing